In [0]:
import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
import csv
import random
import re
import os
import unicodedata
import codecs
import itertools

In [0]:
CUDA = torch.cuda.is_available()
device = torch.device("cuda" if CUDA else "cpu")

In [3]:
device

device(type='cuda')

In [4]:
from zipfile import ZipFile

file = "data.zip"

with ZipFile(file,'r') as zip:
    zip.extractall()
    print('done')

done


In [0]:
#line file  
lines_filepath = os.path.join("cornell movie-dialogs corpus","movie_lines.txt")
#conversation file
con_filepath = os.path.join("cornell movie-dialogs corpus","movie_conversations.txt")

In [6]:
#visualize some lines
#as its already 'utf-8' coded so this codec can't decode byte 0xad thats why insted read i.e 'r' use 'rb'
with open(lines_filepath,'rb') as file:
    lines =file.readlines()
for line in lines[:8]:
    print(line.strip())

b'L1045 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ They do not!'
b'L1044 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ They do to!'
b'L985 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ I hope so.'
b'L984 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ She okay?'
b"L925 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ Let's go."
b'L924 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ Wow'
b"L872 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ Okay -- you're gonna need to learn how to lie."
b'L871 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ No'


In [0]:
#split each line of the file into a dictionary of feilds (lineId,characterId,movieId,character,text)

line_fields = ["lineId","characterId","movieId","character","text"]
lines ={}
#encode in ASCII
with open(lines_filepath,'r',encoding='iso-8859-1') as f:
    for line in f:
        values = line.split(' +++$+++ ')
        #extract fields
        lineObj = {}
        for i, field in enumerate(line_fields):
            #lineObj is dictionary which contaion all lines_fields as key and values
            lineObj[field] = values[i]
        #key for lines dictionary is lineIdand value is lineObj
        lines[lineObj["lineId"]] = lineObj

In [8]:
#1st element of lines dictionary
l = lines
list(l.items())[0]

('L1045',
 {'character': 'BIANCA',
  'characterId': 'u0',
  'lineId': 'L1045',
  'movieId': 'm0',
  'text': 'They do not!\n'})

In [9]:
lines['L194']

{'character': 'BIANCA',
 'characterId': 'u0',
 'lineId': 'L194',
 'movieId': 'm0',
 'text': 'Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.\n'}

In [10]:
#visualize some conversation file
with open(con_filepath,'r') as file:
    convs =file.readlines()
for line in convs[:8]:
    print(line.strip())

u0 +++$+++ u2 +++$+++ m0 +++$+++ ['L194', 'L195', 'L196', 'L197']
u0 +++$+++ u2 +++$+++ m0 +++$+++ ['L198', 'L199']
u0 +++$+++ u2 +++$+++ m0 +++$+++ ['L200', 'L201', 'L202', 'L203']
u0 +++$+++ u2 +++$+++ m0 +++$+++ ['L204', 'L205', 'L206']
u0 +++$+++ u2 +++$+++ m0 +++$+++ ['L207', 'L208']
u0 +++$+++ u2 +++$+++ m0 +++$+++ ['L271', 'L272', 'L273', 'L274', 'L275']
u0 +++$+++ u2 +++$+++ m0 +++$+++ ['L276', 'L277']
u0 +++$+++ u2 +++$+++ m0 +++$+++ ['L280', 'L281']


In [0]:
#split each onversation of the file into a dictionary of feilds ("character1Id","character2Id","movieId","utteranceIds")

conv_fields = ["character1Id","character2Id","movieId","utteranceIds"]
conversations =[]
with open(con_filepath,'r',encoding='iso-8859-1') as f:
    for line in f:
        values = line.split(' +++$+++ ')
        convObj = {}
        for i, field in enumerate(conv_fields):
            convObj[field] = values[i]
        lineIds = eval(convObj["utteranceIds"])
        convObj["lines"] = []
        for lineId in lineIds:
            convObj["lines"].append(lines[lineId])
        conversations.append(convObj)


In [12]:
conversations[0]

{'character1Id': 'u0',
 'character2Id': 'u2',
 'lines': [{'character': 'BIANCA',
   'characterId': 'u0',
   'lineId': 'L194',
   'movieId': 'm0',
   'text': 'Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.\n'},
  {'character': 'CAMERON',
   'characterId': 'u2',
   'lineId': 'L195',
   'movieId': 'm0',
   'text': "Well, I thought we'd start with pronunciation, if that's okay with you.\n"},
  {'character': 'BIANCA',
   'characterId': 'u0',
   'lineId': 'L196',
   'movieId': 'm0',
   'text': 'Not the hacking and gagging and spitting part.  Please.\n'},
  {'character': 'CAMERON',
   'characterId': 'u2',
   'lineId': 'L197',
   'movieId': 'm0',
   'text': "Okay... then how 'bout we try out some French cuisine.  Saturday?  Night?\n"}],
 'movieId': 'm0',
 'utteranceIds': "['L194', 'L195', 'L196', 'L197']\n"}

In [0]:
#making question and amswer pair of each conversation  
qa_pairs =[]
#iterate through the lines inside conversations list
for conversation in conversations:
  for i in range(len(conversation['lines']) - 1):
    inputLine = conversation['lines'][i]['text'].strip()
    targetLine = conversation['lines'][i+1]['text'].strip()
    #if either inputLine or targetLine is absent than ignore
    if inputLine and targetLine:
      qa_pairs.append([inputLine,targetLine])

In [14]:
print(qa_pairs[0])
# total number of conversations
print('length of coversations = {}'.format(len(qa_pairs)))

['Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.', "Well, I thought we'd start with pronunciation, if that's okay with you."]
length of coversations = 221282


In [15]:
#creae new file contain each line with questions and ansers which is seprated by tab

datafile = os.path.join("cornell movie-dialogs corpus","formatted_movie_lines.txt")
delimiter = '\t' #tab
#unescape or decode the delimiter
delimiter = str(codecs.decode(delimiter,'unicode_escape'))

#now write into newly created file
print('start writing into the file...')

#open newly created file and start writing each line with questions and answers which are seprated by tab
with open (datafile, 'w', encoding='utf-8') as outputfile:
  writer  = csv.writer(outputfile, delimiter=delimiter)
  for pair in qa_pairs:
    writer.writerow(pair)
print('\ndone writing')


start writing into the file...

done writing


In [16]:
#visualize some lines inside 'formatted_movie_lines.txt' file

datafile = os.path.join("cornell movie-dialogs corpus","formatted_movie_lines.txt")

with open(datafile,'rb') as file:
  lines = file.readlines()
#1st 8 lines each line contain question and answer which are seprated by '\t'
# and each question answer pair seprated by '\r\n'
for line in lines[:8]:
  print(line)

b"Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.\tWell, I thought we'd start with pronunciation, if that's okay with you.\r\n"
b"Well, I thought we'd start with pronunciation, if that's okay with you.\tNot the hacking and gagging and spitting part.  Please.\r\n"
b"Not the hacking and gagging and spitting part.  Please.\tOkay... then how 'bout we try out some French cuisine.  Saturday?  Night?\r\n"
b"You're asking me out.  That's so cute. What's your name again?\tForget it.\r\n"
b"No, no, it's my fault -- we didn't have a proper introduction ---\tCameron.\r\n"
b"Cameron.\tThe thing is, Cameron -- I'm at the mercy of a particularly hideous breed of loser.  My sister.  I can't date until she does.\r\n"
b"The thing is, Cameron -- I'm at the mercy of a particularly hideous breed of loser.  My sister.  I can't date until she does.\tSeems like she could get a date easy enough...\r\n"
b'Why?\tUnsolved myster

# processing the words

eah line contain                                     

*pad token : if any sentence is shorter than pad it with zero to make all sentence same in length                                    
*start of sentence token(SOS token) : indicate the start of sentence                  
*End of sentence token(EOS token) : indicate the end of sentence 



NOTE :
addword() method is called 2 times                              
>>> *1st time : for counting the number of occurence in sentence using addSentence() method                                                           
>>> *2nd time : for deciding which words are importent and should be keept in dictionary and which are not importent should be removed from dictionary (depending upon number of occurence of that word if less than min_count which is nothing but thershokd than remove else keep).      this call in trim() method

In [0]:
PAD_token = 0
SOS_token = 1
EOS_token = 2

class vocabulary:
  def __init__(self,name):
    self.name = name
    self.word2index = {} #contain word as key and index as value e.g {'hi':0,'he':1,'maybe':2}
    self.word2count = {} #contain word as key and freq i.e number of occurence as value
    #index2word is opposite of word2index which contain index as key and word as value
    self.index2word = {PAD_token : 'PAD', 'SOS_token':'SOS', 'EOS_token':'EOS'}
    #count number of words in conversation (it will start with 3 because we already have 'PAD' = 0,'SOS' =1 & 'EOS'=2)
    self.num_words = 3

  def addSentence(self, sentence):
    """
    sentence.split() convert sentence into list of words
    e.g, inut :'hi i am ankit' ; output:['hi','i','am','ankit']
    """
    for word in sentence.split():
      self.addword(word)
  
  def addword(self,word):
    #check if word is present in the word2index dictionary or not
    if word not in self.word2index:
      self.word2index[word] = self.num_words #new word start with value as 3beacuse already PAD,SOS,EOS is present
      self.word2count[word] = 1 #start counting word occurence
      self.index2word[self.num_words] = word #start key with 3 and value as new word
      self.num_words += 1 #increse the num_words for new word in sentence
    else:
      self.word2count[word] += 1 #count the number of occurence
      
  def trim(self,min_count):
    keep_words = []
    for k,v in self.word2count.items():
      if v >= min_count:
        keep_words.append(k)
    print('keep words {} / {} = {:.4f}'.format(len(keep_words),len(self.word2index),len(keep_words)/len(self.word2index)))
    #reinitialize dictionaries for storing only required words and remove wich are lesser than thershold
    self.word2index = {}
    self.word2count = {}
    self.index2word = {PAD_token : 'PAD', 'SOS_token':'SOS', 'EOS_token':'EOS'}
    self.num_words = 3

    for word in keep_words:
      self.addword(word)

#Data preprocessing

In [0]:
#turn a unicode string into plain ASCII 
def unicodeToAscii(string):
  """
  'NFD': normal form decompose , 'Mn' : non marking
  in unicodedata.normalize() method we pass two arguments one is NFD and string 
  if it is 'Mn' than ignore, this method output as tuple and at the end we combine all element in tupe by join methode
  """
  return ''.join(c for c in unicodedata.normalize('NFD',string) if unicodedata.category(c) != 'Mn')

In [19]:
#example of above method (it convert complex text into plain text by removing all special characctor)
unicodeToAscii('Jaimerais,bière,Où,es-tu ....')

'Jaimerais,biere,Ou,es-tu ....'

Now let's conert all characters in string into lowercase, multiple whites paces into single white space,...etc 
and also remove non-letter characters(i.e either number or sppecial characters)


In [0]:
def normalization(string):
  #convert string into lower case charactors and remove left and right white spaces
  s = unicodeToAscii(string.lower().strip())
  #replace '.' with ' .', '!' with ' !', '?' with ' ?' (i.e white space + chracter)
  # r is use to not consider ' \1' as character(r is to escape backspace)
  # \1 meanse 1st bracketed group
  s = re.sub(r"([.!?])",r" \1",s)
  # remove any character which is not sequesnce of lower letters or either any of . ! ? this 3 special charecters.
  # + means one or more (e.g input : aaa12a ; output : aaa a)
  s = re.sub(r"[^a-zA-Z.!?]+", r" ", s)
  # if mutiple white spaces than replce by single space (i.e input :'    '; output:' ')
  s = re.sub(r"\s+",r" ",s).strip()
  return s

In [21]:
#test above function 
normalization("aa123aBc!s's    dd?")

'aa abc !s s dd ?'

#processing the text inside "formatted_mvie_lines.txt" file

In [22]:
datafile = os.path.join("cornell movie-dialogs corpus","formatted_movie_lines.txt")
#read file and split each line (i.e \n)
print("reading file......")
lines = open(datafile, encoding = 'utf-8').read().strip().split('\n')
# split each line into pairs and normalize them( after spliting each line by '\t' we get one list for each line which contain 2 elements question and answer)
pairs = [[normalization(s) for s in pair.split('\t')] for pair in lines]
print('done reading!')

voc = vocabulary('cornell movie-dialogs corpus')

reading file......
done reading!


In [23]:
#above function results
print("1. single line of conversation in file is as below : ")
print(lines[0])  
print("\n 2. after splitinig by '\t' :")
print(lines[0].split('\t'))
print("\n 3. after normalization of both the elements in list using we created 'normalization' method:")
print(pairs[0])

1. single line of conversation in file is as below : 
Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.	Well, I thought we'd start with pronunciation, if that's okay with you.

 2. after splitinig by '	' :
['Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.', "Well, I thought we'd start with pronunciation, if that's okay with you."]

 3. after normalization of both the elements in list using we created 'normalization' method:
['can we make this quick ? roxanne korrine and andrew barrett are having an incredibly horrendous public break up on the quad . again .', 'well i thought we d start with pronunciation if that s okay with you .']


#filtering the text

In [0]:
#if number of words in either question or answer is gretter than length of 9 than remove
max_len =10

def filterPair(p):
  #pair[0] is 1st element and pair[1] is 2nd element is each list inside pairs list(pairs is list contain multile lists)
  return [pair for pair in pairs if len(pair[0].split()) < max_len and len(pair[1].split()) < max_len]

In [25]:
print('before filteration of pairs , there are {} pairs/conversations \n'.format(len(pairs)))
pairs = filterPair(pairs)
print('after filteration of pairs , there are {} pairs/conversations'.format(len(pairs)))

before filteration of pairs , there are 221282 pairs/conversations 

after filteration of pairs , there are 64271 pairs/conversations


# Let's remove rarely use words

In [26]:
  #loop throw the filtered pairs and pass through the vocabulary class which we created 
  voc = vocabulary('cornell movie-dialogs corpus')
  for pair in pairs:
    voc.addSentence(pair[0]) #question
    voc.addSentence(pair[1]) #reply
  print("number of words : ", voc.num_words)

  #visualize some of the pairs

  for pair in pairs[:10]:
    print(pair)

number of words :  18007
['there .', 'where ?']
['you have my word . as a gentleman', 'you re sweet .']
['hi .', 'looks like things worked out tonight huh ?']
['you know chastity ?', 'i believe we share an art instructor']
['have fun tonight ?', 'tons']
['well no . . .', 'then that s all you had to say .']
['then that s all you had to say .', 'but']
['but', 'you always been this selfish ?']
['do you listen to this crap ?', 'what crap ?']
['what good stuff ?', 'the real you .']


In [27]:
"""
loop through pairs and take only those pair which contain numbers which occures more than thershold 
if any of the word occurence is less than thershold than whole question and reply pair will remove
"""

min_count = 3 #threshold
#voc : object of vocabulary class; pairs : output from above cell; min_count : threshold

def trimRareWords(voc, pairs, min_count):
  voc.trim(min_count) # trim is a method from vocabulary class gives word2index, word2count and index2words dictionaries
  keep_pairs = []
  for pair in pairs:
    input_sentence = pair[0]
    output_sentence = pair[1]
    keep_input = True  # default true if not present in word2index dictionary than set to false
    keep_output = True  # default true if not present in word2index dictionary than set to false
    #check if any of the word in pair[0] and pair[1] (i.e question and reply) is not present in word2index dictionary than remove whole pair of conversation 
    #check for pair[0] (question)
    for word in input_sentence.split(' '):
      if word not in voc.word2index: 
        keep_input = False
        break
    
    #check for pair[1] (reply)
    for word in output_sentence.split(' '):
      if word not in voc.word2index: 
        keep_output = False
        break

    #only keep if keep_input & keep_output both are true 
    if keep_input and keep_output:
      keep_pairs.append(pair)
  print(" trimmed from {} pairs to {}, {:.4f} of total".format(len(pairs), len(keep_pairs),  len(keep_pairs)/ len(pairs)))
  return keep_pairs

pairs = trimRareWords(voc, pairs, min_count)

keep words 7822 / 18004 = 0.4345
 trimmed from 64271 pairs to 53125, 0.8266 of total


# preapering data for model

In [0]:
"""
get index of each word in sentence with end of sentence 
e.g index of 'hi' = 0, 'hello'=1, EOS(end f sentence) =2
input :'hi hello'; output:[0,1,2]
"""

def indexesFromSentence(voc,sentence):
  #word2index is a dictionary which contai word as key and index as value
  return [voc.word2index[word] for word in sentence.split(' ')] + [EOS_token]

In [29]:
print('sentence : ',pairs[1][0])
print('index of each word in sentence :', indexesFromSentence(voc,pairs[1][0]))
print('number of words in sentence {} + 1(EOS_token) = {}'.format(len(pairs[1][0].split()), len(pairs[1][0].split())+1) )

sentence :  you have my word . as a gentleman
index of each word in sentence : [7, 8, 9, 10, 4, 11, 12, 13, 2]
number of words in sentence 8 + 1(EOS_token) = 9


In [30]:
#lets try with some pairs 
questions = []
replys = []
for pair in pairs[:10]:
  questions.append(pair[0])
  replys.append(pair[1])
#let only print questions
print(questions)
print(len(questions))
indexes = [indexesFromSentence(voc, sentence) for sentence in questions]
print(indexes)
print('each list contain 2 at end which shows end of sentence')

['there .', 'you have my word . as a gentleman', 'hi .', 'have fun tonight ?', 'well no . . .', 'then that s all you had to say .', 'but', 'do you listen to this crap ?', 'what good stuff ?', 'wow']
10
[[3, 4, 2], [7, 8, 9, 10, 4, 11, 12, 13, 2], [16, 4, 2], [8, 31, 22, 6, 2], [33, 34, 4, 4, 4, 2], [35, 36, 37, 38, 7, 39, 40, 41, 4, 2], [42, 2], [47, 7, 48, 40, 45, 49, 6, 2], [50, 51, 52, 6, 2], [58, 2]]
each list contain 2 at end which shows end of sentence


In [31]:
"""
 *there is difference between 'zip' & 'zip_longest'
 *'zip_longest' is a method of itertools class
 *we prefere 'zip_longest' insted of 'zip' because for 'zip' need to have all list/tuples same number of elements 
  else it willremove extra elements but in 'zip_longest' it will give 'None' value 
"""
a = [1,2,3,4]
b = [4,5,6]
print(list(itertools.zip_longest(a,b)))
 
# if we want '0' insted of 'None'
print(list(itertools.zip_longest(a,b,fillvalue=0))) 
#we can give any value as fillvalue
print(list(itertools.zip_longest(a,b,fillvalue='d'))) 


[(1, 4), (2, 5), (3, 6), (4, None)]
[(1, 4), (2, 5), (3, 6), (4, 0)]
[(1, 4), (2, 5), (3, 6), (4, 'd')]


In [32]:
#let's start with zeropadding i.e give 0 value if value is not present
"""
as we know max length of any nested list will be 10
we declare during 'filtering the text' in filterPair() method
so if length of any nested list is less than 10 than it will pad with 0 to make length eqqal to 10
"""
nested_list = [[3, 4, 2], 
              [7, 8, 9, 10, 4, 11, 12, 13, 2], 
              [16, 4, 2], 
              [8, 31, 22, 6, 2], 
              [33, 34, 4, 4, 4, 2], 
              [35, 36, 37, 38, 7, 39, 40, 41, 4, 2], 
              [42, 2], [47, 7, 48, 40, 45, 49, 6, 2], 
              [50, 51, 52, 6, 2],
              [58, 2]]

# we know max length is 10 but still let check for it
leng = [len(ind) for ind in nested_list]
print("length of each list inside 'nested_list' : {}\n ".format(leng))
print('maximum length is', max(leng))

length of each list inside 'nested_list' : [3, 9, 3, 5, 6, 10, 2, 8, 5, 2]
 
maximum length is 10


In [0]:
def zerPadding(l,fillvalue = 0):
  return list(itertools.zip_longest(*l, fillvalue= fillvalue))

In [34]:
#let test zeroPadding() function on 'nested_list'
test_result = zerPadding(nested_list)
print(test_result)

[(3, 7, 16, 8, 33, 35, 42, 47, 50, 58), (4, 8, 4, 31, 34, 36, 2, 7, 51, 2), (2, 9, 2, 22, 4, 37, 0, 48, 52, 0), (0, 10, 0, 6, 4, 38, 0, 40, 6, 0), (0, 4, 0, 2, 4, 7, 0, 45, 2, 0), (0, 11, 0, 0, 2, 39, 0, 49, 0, 0), (0, 12, 0, 0, 0, 40, 0, 6, 0, 0), (0, 13, 0, 0, 0, 41, 0, 2, 0, 0), (0, 2, 0, 0, 0, 4, 0, 0, 0, 0), (0, 0, 0, 0, 0, 2, 0, 0, 0, 0)]


test_result =  

[(3, 7, 16, 8, 33, 35, 42, 47, 50, 58),                                              
(4, 8, 4, 31, 34, 36, 2, 7, 51, 2),                             
(2, 9, 2, 22, 4, 37, 0, 48, 52, 0),                                
(0, 10, 0, 6, 4, 38, 0, 40, 6, 0),                                  
(0, 4, 0, 2, 4, 7, 0, 45, 2, 0),                                    
(0, 11, 0, 0, 2, 39, 0, 49, 0, 0),                                     
(0, 12, 0, 0, 0, 40, 0, 6, 0, 0),                                 
(0, 13, 0, 0, 0, 41, 0, 2, 0, 0),                                          
(0, 2, 0, 0, 0, 4, 0, 0, 0, 0),                                         
(0, 0, 0, 0, 0, 2, 0, 0, 0, 0)]                                                     
  
***
[1]. where 1st tuple contain 1st elements of each list inside 'nested_list', 2nd tuple contain 2nd elements of each list inside 'nested_list', 3rd tuple contain 3rd elements of each list inside 'nested_list', and so on .... 
***
[2].  and if element not prsesnt in list it will put 0 in tuple.
***
[3]. now max length is number of rows as we interchange rows and columns.
***
[4]. each element in list is nothing but token/index number of each word
***


#Prepare data for our Model(input data)  :

#BInary Matrix Formation

les't create binary matrix 

In [0]:
def binaryMatrix(l, value = 0):
  inp_matrix = []
  for i,lis in enumerate(l):
    inp_matrix.append([])
    for elem in lis:
      if elem == 0:
        inp_matrix[i].append(0)
      else:
        inp_matrix[i].append(1)
  return inp_matrix

In [36]:
#test above function with 'test_result' matrix
result = binaryMatrix(test_result)
result

[[1, 1, 1, 1, 1, 1, 1, 1, 1, 1],
 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1],
 [1, 1, 1, 1, 1, 1, 0, 1, 1, 0],
 [0, 1, 0, 1, 1, 1, 0, 1, 1, 0],
 [0, 1, 0, 1, 1, 1, 0, 1, 1, 0],
 [0, 1, 0, 0, 1, 1, 0, 1, 0, 0],
 [0, 1, 0, 0, 0, 1, 0, 1, 0, 0],
 [0, 1, 0, 0, 0, 1, 0, 1, 0, 0],
 [0, 1, 0, 0, 0, 1, 0, 0, 0, 0],
 [0, 0, 0, 0, 0, 1, 0, 0, 0, 0]]

test_result =  

[(3, 7, 16, 8, 33, 35, 42, 47, 50, 58),                                              
(4, 8, 4, 31, 34, 36, 2, 7, 51, 2),                             
(2, 9, 2, 22, 4, 37, 0, 48, 52, 0),                                
(0, 10, 0, 6, 4, 38, 0, 40, 6, 0),                                  
(0, 4, 0, 2, 4, 7, 0, 45, 2, 0),                                    
(0, 11, 0, 0, 2, 39, 0, 49, 0, 0),                                     
(0, 12, 0, 0, 0, 40, 0, 6, 0, 0),                                 
(0, 13, 0, 0, 0, 41, 0, 2, 0, 0),                                          
(0, 2, 0, 0, 0, 4, 0, 0, 0, 0),                                         
(0, 0, 0, 0, 0, 2, 0, 0, 0, 0)]     

******
it shows that each tuple converted to list & if element is 'non zero' than put '1' and if element is 'zero' than put '0'
***

resullt =                                                                     
[[1, 1, 1, 1, 1, 1, 1, 1, 1, 1],                                                      
 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1],                                                         
 [1, 1, 1, 1, 1, 1, 0, 1, 1, 0],                                                            
 [0, 1, 0, 1, 1, 1, 0, 1, 1, 0],                                      
 [0, 1, 0, 1, 1, 1, 0, 1, 1, 0],                                                           
 [0, 1, 0, 0, 1, 1, 0, 1, 0, 0],                                                        
 [0, 1, 0, 0, 0, 1, 0, 1, 0, 0],                                                         
 [0, 1, 0, 0, 0, 1, 0, 1, 0, 0],                                                            
 [0, 1, 0, 0, 0, 1, 0, 0, 0, 0],                                                         
 [0, 0, 0, 0, 0, 1, 0, 0, 0, 0]]                                                                                                                                           

# Input data for model

In [0]:
"""
1.this function takes the list of all 'questions' in the conversation as input and returs padded input sequesce 
than we convert that padded input senquence into 'torch.tensor' format for model and also take the length of each
batch inside tensor
"""
#l = list of questions ; voc = vocabulary class obet

def inputVar(l,voc):
  #indexesFromSentence() this fuction gives us the list of indexes for each sentence/question
  indexes_batch = [indexesFromSentence(voc, sentence) for sentence in l]
  #take the length of each list of indexes & conver list into torch.tensor()
  lengths = torch.tensor([len(indexes) for indexes in indexes_batch])
  # padding operation using zeroPadding() function
  padList = zerPadding(indexes_batch)
  #convert padList into torch.tensor() with each element is of long type
  padVar = torch.LongTensor(padList)
  #return padded torch tensor & length of each list inside tensor
  return padVar, lengths

In [0]:
"""
this function contain some operation similar as above function & some extra operations

for this fuction we take list of all 'reply' as input, convert each word of reply/sentence into list of indexes(i.e each index number for each words),
take the maximum length among all the list of indexes, do padding operation 

now use padding operation as input and perform 2 operations,
1. output of padding operation -> perform binary operation to get 1s and 0s -> convert into torch byte tensor
2. output of padding operation -> convert each integer into long type

3 OUTPUT of function:
maximum length, tensor with all long type, byte tensors
"""
#l = list of questions ; voc = vocabulary class obet
def outputVar(l, voc):
  #indexesFromSentence() this fuction gives us the list of indexes for each sentence/question
  indexes_batch = [indexesFromSentence(voc, sentence) for sentence in l]
  #take the maximum length among the list of length
  max_length = max([len(indexes) for indexes in indexes_batch])
  # padding operation using zeroPadding() function
  padList = zerPadding(indexes_batch)
  #convert padList into list of 1s and 0s
  mask = binaryMatrix(padList)
  #convert mask list into byte tensor
  mask = torch.ByteTensor(mask)
  #convert each elemnt of padList into Long type
  padVar = torch.LongTensor(padList)
  #3 output of function is 1.tensor with all long type, 2.byte tensors, 3.maximum length
  return padVar, mask, max_length


In [0]:
#voc = object of vocabulary class; pair_batch = it is nested list and each lit contain 2 elements question,answer  
def batch2TrainData(voc, pair_batch):
  #each list inside pair_batch 1st-elment is question & 2nd is answer,now sort the pair_batch list by length of question
  pair_batch.sort(key = lambda x: len(x[0].split(' ')), reverse = True)
  input_batch,output_batch = [],[]
  for pair in pair_batch:
    input_batch.append(pair[0])
    output_batch.append(pair[1])
  #use inputVar() & outputVar() function's which are created above
  inp, lengths = inputVar(input_batch, voc)
  output, mask, max_length = outputVar(output_batch, voc)
  return inp, lengths, output, mask, max_length
  

In [40]:
"""
pairs is a nested list, in which each list contain 2 elements 1st is question and 2nd is answer
"""
#take 1st 5 list inside pairs-list
lis = []
for i in range(5):
  lis.append(pairs[i])

#let test batch2TrainData() function 
inp, lengths, output, mask, max_length = batch2TrainData(voc, lis)
print('input variables :')
print(inp)
print('\n list of lengths of each sentence : ', lengths)
print('\n target variables :')
print(output)
print('\n byte tensor :')
print(mask)
print('\n maximum length among output tensors :', max_length)

input variables :
tensor([[ 7, 33,  8,  3, 16],
        [ 8, 34, 31,  4,  4],
        [ 9,  4, 22,  2,  2],
        [10,  4,  6,  0,  0],
        [ 4,  4,  2,  0,  0],
        [11,  2,  0,  0,  0],
        [12,  0,  0,  0,  0],
        [13,  0,  0,  0,  0],
        [ 2,  0,  0,  0,  0]])

 list of lengths of each sentence :  tensor([9, 6, 5, 3, 3])

 target variables :
tensor([[ 7, 35, 32,  5, 17],
        [14, 36,  2,  6, 18],
        [15, 37,  0,  2, 19],
        [ 4, 38,  0,  0, 20],
        [ 2,  7,  0,  0, 21],
        [ 0, 39,  0,  0, 22],
        [ 0, 40,  0,  0, 23],
        [ 0, 41,  0,  0,  6],
        [ 0,  4,  0,  0,  2],
        [ 0,  2,  0,  0,  0]])

 byte tensor :
tensor([[1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1],
        [1, 1, 0, 1, 1],
        [1, 1, 0, 0, 1],
        [1, 1, 0, 0, 1],
        [0, 1, 0, 0, 1],
        [0, 1, 0, 0, 1],
        [0, 1, 0, 0, 1],
        [0, 1, 0, 0, 1],
        [0, 1, 0, 0, 0]], dtype=torch.uint8)

 maximum length among output tensors : 1

# Start with Model

we are using RNN model (GRU)

![alt text](https://miro.medium.com/max/3032/1*yBXV9o5q7L_CvY7quJt3WQ.png
)

#SEquence to Sequence GRU Model

It contain 'Encoder' & 'Decoder'

![alt text](https://cntk.ai/jup/s2s.png)

We are using "Bidirectional-GRU", means there is 2 independent RNN
1. fed the input sequence in normal sequential order
2. fed the input squence in reverse order

# define Encoder Class

In [0]:
#inherit from 'nn' class  'Module' method from pytorch package 
class EncoderRNN(nn.Module):
  #create constructor
  """
  hidden_size = number of nuerons in hidden lay,
  embedding = searching/learning for words that have same meaning as given input word, 
  n_layers = number of hidden layers,
   dropout = % of drop neurons from hidden layer
  """
  def __init__(self, hidden_size, embedding, n_layers =1, dropout =0):
    #inherit from super class
    super(EncoderRNN, self).__init__()
    self.hidden_size = hidden_size
    self.embedding = embedding
    self.n_layers = n_layers
    #set 'input_size' & 'hidden_size' parameters equal to 'hiden_size'
    #we are using embedding (look in the pytorch documentaion for more details)
    #initialize GRU: nn.GRU(input_size,hidden_size,n_layers, dropout, bidirectional)
    self.gru = nn.GRU(hidden_size, hidden_size, n_layers, dropout=(0 if n_layers ==1 else dropout), bidirectional = True)

  #forward propagation
  """
  input_seq = bath of input sentence, each of shape=(max_length, batch_size),
  input_lengths = list of each sentence length,
  hidden = hidden state between each channel, shape =(n_layers * num_directions, batch_size, hidden_size)  
  """
  def forward(self, input_seq, input_lengths, hidden = None):
    embedded = self.embedding(input_seq)
    #we can either use pack padded or normal (in this RNN we are using pack padded inputs)
    packed = torch.nn.utils.rnn.pack_padded_sequence(embedded, input_lengths)
    #forward pass through GRU
    output, hidden = self.gru(packed,hidden)
    #unpack padding
    outputs,_ = torch.nn.utils.rnn.pad_packed_sequence(output)
    #take the sum of both GRU (Bidirectional GRU)
    outputs = outputs[:, :, :self.hidden_size] + outputs[:, :, self.hidden_size:]
    # it will return output and final hidden state (more details on documentation of pytorch)
    return outputs, hidden

    """
    outputs: the output feature from the last layer of the GRU, for each timestep(sum of bidirectional outputs)
    outputs shape = (max_length, batch_size, hidden_size)
    
    hidden: hidden state from the last timestep only, of shape=(n_layers * num_directions, batch_size, hidden_size)
    """



# Define the Decoder with Attention mechanism

In [0]:
#Attention Class

#inherti from torch.nn.Module
class Attn(torch.nn.Module):
  def __init__(self, method, hidden_size):
    super(Attn, self).__init__()
    self.method = method
    self.hidden_size = hidden_size

  #elemnet wise multiplication of encoder_output & current GRU decoder state
  def dot_product(self, hidden, encoder_output): 
    return torch.sum(hidden * encoder_output, dim = 2)

  
  """
  encoder_output: of shape=(max_length, batch_size, hidden_size)
  hidden: of shape=(1, batch_size, hidden_size) ; 1 becuse each GRU have only one element
  
  after taking dot product of hidden & encoder_output we will get:
  (max_length, batch_size, hidden_size) * (1, batch_size, hidden_size) = (max_length, batch_size, hidden_size)
    
  dim=2 in dot_product() function means addition of last 2 dimension (i.e  batch_size + hidden_size)
  which is of size batch_size 
  so the output of dot_product() function is (max_length, batch_size)
  """
  def forward(self, hidden, encoder_outputs):
    attn_engergies = self.dot_product(hidden, encoder_outputs) #(max_length, batch_size)
    #transpose max_length & batch_size dimensions
    attn_engergies = attn_engergies.t() #(batch_size, max_length)
    #now perform softmax normalization(with added dimension)
    return F.softmax(attn_engergies, dim =1).unsqueeze(1) #(batch_size, 1, max_length)

    #f is a function which is imported 

In [0]:
#decoder class

#inherit from nn.Module
class LuongAttnDecoderRNN(nn.Module):
  #create constructor
  """
  attn_model = model that we are providing in 'Attension Mechanism' 
  embedding = searching/learning for words that have same meaning as given input word, 
  hidden_size = number of nuerons in hidden lay,
  output_size = output matrix size, of shape = (max_length, batch_size, hidden_size),
  n_layers = number of hidden layers,
   dropout = % of drop neurons from hidden layer
  """
  def __init__(self, attn_model, embedding, hidden_size, output_size, n_layers =1, dropout =0.1):
    super(LuongAttnDecoderRNN, self).__init__()
    self.attn_model = attn_model
    self.hidden_size = hidden_size
    self.output_size = output_size
    self.n_layers = n_layers
    self.dropout = dropout

    #define layers
    self.embedding = embedding
    self.embedding_dropout = nn.Dropout()  #also we are using dropout for embedding
    #bidirection is false
    self.gru = nn.GRU(hidden_size, hidden_size, n_layers, dropout=(0 if n_layers ==1 else dropout))
    #after concatinating attension model output & GRU output we get size of (bach_size, hidden_size *2)
    #for perfoming 'tanh operation we converting this into (hidden_size * 2, hidden_size)
    self.concat = nn.Linear(hidden_size * 2, hidden_size)
    #befor putting into softmax we agin convert it into (hidden_size, output_size)
    self.out = nn.Linear(hidden_size, output_size)

    self.attn = Attn(attn_model, hidden_size)

  #forward from one GRU to another at 'Decoder'
  """
  input_step = one time step of input sequence for predincting one word(1st GRE), of shape=(1, batch_size)
  last_hidden = hidden state from last GRU, of shape = (n_layers * num_directions, batch_size, hidden_size)
  encoder_output = encoder model's output, of shape = (ax_length, batch_size, hidden_size)
  """
  def forward(self, input_step, last_hidden, encoder_output):
    # 1.embedding current input words (batch)
    embedded = self.embedding(input_step)
    # 2.perform dropout on embedded output
    embedded = self.embedding_dropout(embedded)
    # 3.forward pass through unidirectional GRU
    rnn_output, hidden = self.gru(embedded, last_hidden)
    # 4.calculating the attention weights from the current GRU mmodel output
    attn_weights = self.attn(rnn_output, encoder_output)
    # 5. context vector/weighted sum = attention weights * encoder outputs
    #bmm = batch multiplication mechanisum
    #(batch_size,1,max_length) bmm (batch_size, max_length, hidden) = (batch_size, 1 , hidden)
    #matrix multiplication, (1, max_length) matrix multiplication (max_length, hidden) = (1,hidden)
    #so the context shape= (batch_size, 1, hidden)
    context = attn_weights.bmm(encoder_output.transpose(0,1)) 
    # 6. we have GRU output 'rnn_output' shape=(1, batch_size, hidden_size) & context shape= (batch_size, 1, hidden)
    #    remove 1 by using squeeze
    rnn_output = rnn_output.squeeze(0) # 0 is position in shape
    context = context.squeeze(1) # 1 is position in shape
    # 7. concate GRU output shape = (batch_size, hidden_size) & context vector = (batch_size, hidden_size)
    # 1 is dimention number i.e column
    #concatination result shape = (batch_size, hidden_size * 2)
    concat_input = torch.cat((rnn_output,context), 1) 
    # 8. pass concat_input through 'Linear layer' to for shape = (batch_size, hidden_size)
    #now this newly created shape is passes through 'tanh' activation function
    #(batch_size, hidden_size) -> tanh -> (batch_size, voc_size)
    concat_output = torch.tanh(self.concat(concat_input)) #self.concat represent Linear layer as we declear in constructor
    # 9. pass concat_output through 'Linear layer' for output prediction
    output = self.out(concat_output) #self.out represent 2nd Linear layer as we declear in constructor
    # 10. pass this outputs through softmax to get ranging between 0-1 for each output
    output = F.softmax(output, dim =1) #dim =1 (1 column)
    #this function returns output & final hidden state which passes for next GRU as input for predicting next word
    return output, hidden
    #output shape = (batch_size, voc_size)
    #hidden = (n_layers * n_directions, batch_size, hidden_size)

# Loss Function
*                                                        we are using 'Teacher Forcing' for o.5 time and remaning 0.5 'No Teacher Forcing' at Training
* 'No Teacher Forcing' at Testing                     

In [0]:
"""
*decoder_output is getting from LuongAttnDecoderRNN lass
*mask and target we are getting from batch2TrainData() function which we created

mask is a matrix of 1s & 0s, we ignore 0s and calculate 'loss' only for 1s
"""
# maskKNLLLoss = mask Negartive Log LikeLihood Loss
def maskKNLLLoss(decoder_out, target, mask):
  nTotal = mask.sum() #this will give us total number of ones/non-zero elements in matrix
  target = target.view(-1,1) #any number of rows that python decide and 1 column
  #decoder shape = (batch_size, voc_size); target = (batch_size,1)
  gathered_tensor = torch.gather(decoder_out,1,target)
  #calculate the loss
  crossEntrophy = -torch.log(gathered_tensor) #NLLLoss( Negartive Log LikeLihood Loss)
  #only select/consider non-zero elements
  loss = crossEntrophy.masked_select(mask)
  #calculate the mean of los
  loss = loss.mean()
  loss = loss.to(device) #convert to currently use device (CPU/GPU/...)
  #return total number of non-zero elements(nTotal), loss
  return loss, nTotal.item()




# Start with Iteration 


#1. Preparing Data for model

In [45]:
#let's take only single time all timestemp

batch_size = 5
#we are taking random 5 [question, reply]from pairs list and pass in batch2TrainData() which we created
batches = batch2TrainData(voc, [random.choice(pair) for _ in range(batch_size)])
#output of batch2TrainData() function
inp_variable, lengths, output_variable, mask, max_length = batch2TrainData(voc, lis)
print('input variables :',inp_variable.shape)
print('\n list of lengths of each sentence : ', lengths.shape)
print('\n target variables :',output_variable.shape)
print('\n byte tensor :', mask.shape)
print('\n maximum length among output tensors :', max_length)

#define the paramters

"""
'Encoder' and 'Decoder' both have different 'RNN'
"""
hidden_size = 500     #number of neurons in hidden layer
encoder_n_layers = 2  #number of hidden layers in encoder RNN
decoder_n_layers = 2  #number of hidden layers in decoder RNN
dropout = 0.1         # % of random cells/neurons dropout at each iteration
attn_model = 'dot'    # attention model

#embedding is nothing but converting each word into vector, vector of size = hidden_size
embedding = nn.Embedding(voc.num_words, hidden_size) #voc.num_words is nothing but number of words we have

#define the encoder & decoder
encoder = EncoderRNN(hidden_size, embedding, encoder_n_layers, dropout)
decoder = LuongAttnDecoderRNN(attn_model, embedding, hidden_size, voc.num_words, decoder_n_layers, dropout)
#applying encoder & decoder to currently using deice CPU/GPU/....
encoder = encoder.to(device)
decoder = decoder.to(device)
#setting in Training mode
encoder.train()
decoder.train()

#initialize optimizer (we are using Adams optimizer)
encoder_optimizer = optim.Adam(encoder.parameters(), lr=0.0001)
decoder_optimizer = optim.Adam(decoder.parameters(), lr=0.0001)
#after each iteration we set gradint to zero so it will not combine with next optimizer
encoder_optimizer.zero_grad() 
decoder_optimizer.zero_grad()

# output of batch2TrainData() = (inp_variable, lengths, output_variable, mask, max_length)
inp_variable = inp_variable.to(device)
lengths = lengths.to(device)
output_variable = output_variable.to(device)
mask = mask.to(device)

loss = 0           #at start loss set to 0
print_losses = []  # print loss for each batch 
n_totals = 0       # number of elements in 'print_losses' list

# Forward pass through encoder
encoder_outputs, encoder_hidden = encoder(inp_variable, lengths)
print(' Encoder Outputs Shape :', encoder_outputs.shape)
print('Last Encoder Hidden state Shape :', encoder_hidden.shape)

# Initiate & Forward pass decoder
decoder_input = torch.LongTensor([[SOS_token for _ in range(batch_size)]]) #list contain SOS_token batch_size i.e 5 
decoder_input = decoder_input.to(device)
print('Initial decoder Input shape :', decoder_input.shape)
print(decoder_input)

#set 1st Decoder hidden state to the last Encoder hidden state
#as n_layers(number of layers) is 2 so we are taking first 2 hidden state of Encoder
decoder_hidden = encoder_hidden[:decoder.n_layers]
print("Initial Decoder hidden state shape: {} \n".format(decoder_hidden.shape))
print("---------------------------------------------------------------------------------------------")
print("Checkout Timestep in GRU ->")
print("--------------------------------------------------------------------------------------------- \n")





input variables : torch.Size([9, 5])

 list of lengths of each sentence :  torch.Size([5])

 target variables : torch.Size([10, 5])

 byte tensor : torch.Size([10, 5])

 maximum length among output tensors : 10
 Encoder Outputs Shape : torch.Size([9, 5, 500])
Last Encoder Hidden state Shape : torch.Size([4, 5, 500])
Initial decoder Input shape : torch.Size([1, 5])
tensor([[1, 1, 1, 1, 1]], device='cuda:0')
Initial Decoder hidden state shape: torch.Size([2, 5, 500]) 

---------------------------------------------------------------------------------------------
Checkout Timestep in GRU ->
--------------------------------------------------------------------------------------------- 



#2. Test for 1 batch(training)

In [46]:
#assume we are using Teachure Forcing at Training time
# max_length getting from batch2TrainData() function
for t in range(max_length):
  decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden, encoder_outputs)
  print("Decoder Output shape :", decoder_output.shape)
  print("Decoder Hidden shape : ", decoder_hidden.shape)
  #Techure Forcing : next GRU input is previous/last GRU target
  decoder_input = output_variable[t].view(1, -1) 
  print("The output_variable at current timestep before reshaping : ", output_variable[t])
  print("The output_variable at current timestep shape before reshaping : ", output_variable[t].shape)
  print("Decoder input shape(after reshaping the output_variable) : ", decoder_input.shape)
  #calculate the loss
  print("mask at current timestep : ", mask[t]) # mask getting from batch2TrainData() function
  print("mask at current timestep : ", mask[t].shape)
  # mask_loss = loss at each timestep, nTotal = total number of non-zero elements at each time step
  mask_loss, nTotal = maskKNLLLoss(decoder_output, output_variable[t], mask[t])
  print("total number of 'non-zero' elements in current batch : ", nTotal)
  print("Mask Loss : ", mask_loss)
  loss += mask_loss  #summing the loss at each timestep
  # multiplying 'loss' by 'number of non-zero elements' at that time-step & appending into 'print_losses' list
  print_losses.append(mask_loss.item() * nTotal)
  print("list of losses at each time-step : ", print_losses)
  n_totals += nTotal   # total number of non-zero elements present in data
  print("Total Number of elements in list(non-zero elements) :",n_totals)
  # .step() function use to 'update tha weights'
  encoder_optimizer.step()
  decoder_optimizer.step()
  loss = sum(print_losses)/n_totals #mean loss/ final loss
  print(" loss : {} \n".format(loss))
  print("----------completed {} timestep----------\n".format(t))




Decoder Output shape : torch.Size([5, 7825])
Decoder Hidden shape :  torch.Size([2, 5, 500])
The output_variable at current timestep before reshaping :  tensor([ 7, 35, 32,  5, 17], device='cuda:0')
The output_variable at current timestep shape before reshaping :  torch.Size([5])
Decoder input shape(after reshaping the output_variable) :  torch.Size([1, 5])
mask at current timestep :  tensor([1, 1, 1, 1, 1], device='cuda:0', dtype=torch.uint8)
mask at current timestep :  torch.Size([5])
total number of 'non-zero' elements in current batch :  5
Mask Loss :  tensor(8.9738, device='cuda:0', grad_fn=<MeanBackward0>)
list of losses at each time-step :  [44.86900329589844]
Total Number of elements in list(non-zero elements) : 5
 loss : 8.973800659179688 

----------completed 0 timestep----------

Decoder Output shape : torch.Size([5, 7825])
Decoder Hidden shape :  torch.Size([2, 5, 500])
The output_variable at current timestep before reshaping :  tensor([14, 36,  2,  6, 18], device='cuda:0')

/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

#Define Function for training

all step same as we test for one batch, only we put inside a function


#combine upper step's 1 & 2

In [0]:
#inp_variable, lengths, output_variable, mask, max_length this are output of batch2TrainData() which we created
def train(inp_variable, lengths, output_variable, mask, max_length, encoder, decoder, embedding, encoder_optimizer, 
                decoder_optimizer, batch_size, clip, maximum_length = max_length):
  
  #set gradirnt to zero
  encoder_optimizer.zero_grad()
  decoder_optimizer.zero_grad()

  #swt arguments according to the device to be use (CPU/GPU/...)
  inp_variable = inp_variable.to(device)
  lengths = lengths.to(device)
  output_variable = output_variable.to(device)
  mask =mask.to(device)

  #initialzation of variables
  loss = 0          
  print_losses = []  
  n_totals = 0

  # Forward pass through encoder
  encoder_outputs, encoder_hidden = encoder(inp_variable, lengths)

  # Initiate & Forward pass decoder
  decoder_input = torch.LongTensor([[SOS_token for _ in range(batch_size)]]) #list contain SOS_token batch_size i.e 5 
  decoder_input = decoder_input.to(device)

  #set 1st Decoder hidden state to the last Encoder hidden state
  #as n_layers(number of layers) is 2 so we are taking first 2 hidden state of Encoder
  decoder_hidden = encoder_hidden[:decoder.n_layers]

  #we are going take "Teacher-Forcing" for 50% of data and "Non_Teacher-Forcing" for reaming data
#randomly chose number if it is more than "teacher_forcing_ratio" than "Non_Teacher-Forcing" else "Teacher-Forcing" 
  use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False
  if use_teacher_forcing:
    for t in range(max_length):
      decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden, encoder_outputs)
      #only difference is we are gona take 'actual-previous output' as Input for next GRU
      decoder_input = output_variable[t].view(1, -1) 
      mask_loss, nTotal = maskKNLLLoss(decoder_output, output_variable[t], mask[t])
      loss += mask_loss 
      print_losses.append(mask_loss.item() * nTotal)
      n_totals += nTotal
  else:
    for t in range(max_length):
      decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden, encoder_outputs)
      #only difference is we are gona take 'previous-predicted output' as Input for next GRU
      _, topi = decoder_output.topk(1) 
      decoder_input = torch.LongTensor([[topi[i][0] for i in range(batch_size)]])
      mask_loss, nTotal = maskKNLLLoss(decoder_output, output_variable[t], mask[t])
      loss += mask_loss 
      print_losses.append(mask_loss.item() * nTotal)
      n_totals += nTotal  

  """
  below steps are new which we does not use till now
  """

  #for "Back-Propagation"
  loss.backward()

  #clip gradient : gradients are modified in place(it is use to prevent from vanishing & exploding gradients)
  _ = torch.nn.utils.clip_grad_norm_(encoder.parameters(),clip)
  _ = torch.nn.utils.clip_grad_norm_(decoder.parameters(),clip)
  #adjust model weights
  encoder_optimizer.step()
  decoder_optimizer.step()

  #final loss which we are getting after each eateration
  return sum(print_losses)/n_totals



# Define function for Iterations

* model_name = "declearing model we are using for Iteration",
* voc = object of vocabulary class which we created,
* pairs = nested list of multiple 'question'&'answer' list, 
* encoder = encoder function, 
* decoder = decoder function, 
* encoder_optimizer = encoder input optimizer, 
* decoder_optimizer = decoder input optimizer,
* embedding = embedding function, 
* encoder_n_layers = number of hidden layer in encoder RNN,
* decoder_n_layers number of hidden layer in decoder RNN,,
* save_dir = create directory/file for saving data,
* n_iteration = number of iterations,
* batch_size = declearing batch size,
* print_every = print every n number of iteration,
* save_every =  save every n number of iteration,
* clip = clip gradient : gradients are modified in place(it is use to prevent from vanishing & exploding gradients)
, 
* loadFilename = loding file from device


In [0]:
def trainIteration(model_name, voc, pairs, encoder, decoder, encoder_optimizer, decoder_optimizer, 
                   embedding, encoder_n_layers, decoder_n_layers, save_dir, n_iteration, 
                   batch_size, print_every, save_every, clip, corpus_name, loadFilename):
  # Load batches for each iteration
  training_batches = [batch2TrainData(voc, [random.choice(pairs) for _ in range(batch_size)])
                      for _ in range(n_iteration)]

  # Initializations Iterations
  print("Initializing Iteration's...")
  start_iteration = 1
  print_loss = 0

  # Training loop for n number of iterations
  print("Start Training...")
  #as start_iteration set to 1, we are adding 1 more iteration
  for iteration in range(start_iteration, n_iteration + 1):
    #as 1st value for 'iteration' is 1 but we want 0, thats why "iteration - 1"
    #1st batch = training_batches[0]
    training_batch = training_batches[iteration - 1]
    # Extract fields from batch
    inp_variable, lengths, output_variable, mask, max_length = training_batch

    # Run a training iteration with batch, train() function
    loss = train(inp_variable, lengths, output_variable, mask, max_length, encoder,
                 decoder, embedding, encoder_optimizer, decoder_optimizer, batch_size, clip)
    print_loss += loss

    # Print progress after every 'n' number of iteration
    if iteration % print_every == 0:
      print_loss_avg = print_loss / print_every
      print("Iteration: {}; Percent complete: {:.1f}%; Average loss: {:.4f}".format(iteration, iteration / n_iteration * 100, print_loss_avg))
      print_loss = 0


In [0]:

"""
checking some torch functions
"""
x = torch.randn(2,2) 
# print(x)
# print("\n")
# a = torch.transpose(x, 0, 1)
# print(a)

# # creating 2 rows 2 columns zero-tensor
# all_zero_tensor = torch.zeros([2,2], device=device, dtype=torch.long) 
# print(all_zero_tensor)
# empty_tensor = torch.zeros([], device=device, dtype=torch.long) # creating empty tensor
# print(empty_tensor)
# # creating 2 rows 2 columns tensor
# t = torch.tensor([[1,2],[3,4]], device=device, dtype=torch.long)
# print(t)
# #concationation operation
# all_tokens = torch.cat((empty_tensor, t), dim=0)
# # print(all_tokens)

#Greedy decoding

Greedy decoding is the decoding method that we use during training when we are NOT using teacher forcing. In other words, for each time step, we simply choose the word from decoder_output with the highest softmax value. This decoding method is optimal on a single time-step level.

In [0]:
class GreedySearchDecoder(nn.Module):
  def __init__(self, encoder, decoder):
    super(GreedySearchDecoder, self).__init__()
    self.encoder = encoder
    self.decoder = decoder

  def forward(self, input_seq, input_length, max_length):
    # Forward input through encoder model
    encoder_outputs, encoder_hidden = self.encoder(input_seq, input_length)
    # Prepare encoder's final hidden layer to be first hidden input to the decoder
    decoder_hidden = encoder_hidden[:decoder.n_layers]
    # Initialize decoder input with SOS_token
    decoder_input = torch.ones(1, 1, device=device, dtype=torch.long) * SOS_token
    # Initialize tensors to append decoded words to (empty tensor)
    all_tokens = torch.zeros([0], device=device, dtype=torch.long)
    all_scores = torch.zeros([0], device=device)
    # Iteratively decode one word token at a time
    for _ in range(max_length):
      # Forward pass through decoder
      decoder_output, decoder_hidden = self.decoder(decoder_input, decoder_hidden, encoder_outputs)
      # Obtain most likely word token and its softmax score
      decoder_scores, decoder_input = torch.max(decoder_output, dim=1)
      # Record token and score
      all_tokens = torch.cat((all_tokens, decoder_input), dim=0)
      all_scores = torch.cat((all_scores, decoder_scores), dim=0)
      # Prepare current token to be next decoder input (add a dimension)
      decoder_input = torch.unsqueeze(decoder_input, 0)
      # Return collections of word tokens and scores
      return all_tokens, all_scores
    

# Evaluate my text

#evaluate() :

this function is responsible for following operation using vocabulory class

* creating indexes for each word in sentence
* converting word2index, index2word

In [0]:
def evaluate(encoder, decoder, searcher, voc, sentence, max_length=max_len):
  ### Format input sentence as a batch
  # words -> indexes
  indexes_batch = [indexesFromSentence(voc, sentence)]
  # Create lengths tensor
  lengths = torch.tensor([len(indexes) for indexes in indexes_batch])
  # Transpose dimensions of batch to match models' expectations
  input_batch = torch.LongTensor(indexes_batch).transpose(0, 1)
  # Use appropriate device
  input_batch = input_batch.to(device)
  lengths = lengths.to(device)
  # Decode sentence with searcher
  tokens, scores = searcher(input_batch, lengths, max_length)
  # indexes -> words
  decoded_words = [voc.index2word[token.item()] for token in tokens]
  return decoded_words

#evaluateInput(): 

this is our 'User Interation' responsible for taking input/sentence from User

We loop this process, so we can keep chatting with our bot until we enter either “q” or “quit”.

If either “q” or “quit” is getting as input bot will stop responding as we give condition in below function

In [0]:
def evaluateInput(encoder, decoder, searcher, voc):
  input_sentence = ''
  while(1):
    try:
      # Get input sentence
      input_sentence = input('> ')
      # Check if it is quit case
      if input_sentence == 'q' or input_sentence == 'quit' or input_sentence == 'byee' :
        print("byee")
        break
      # Normalize sentence
      input_sentence = normalization(input_sentence)
      # Evaluate sentence
      output_words = evaluate(encoder, decoder, searcher, voc, input_sentence)
      # Format and print response sentence
      output_words[:] = [x for x in output_words if not (x == 'EOS' or x == 'PAD')]
      print('A.D:', ' '.join(output_words))

    except KeyError:
      print("Error: Encountered unknown word.")

# Run Model

In [64]:
# Assigning/Declearing value for models
model_name = 'cb_model'
# there are three types of operation are present for 'Attension Model'
attn_model = 'dot'
#attn_model = 'general'
#attn_model = 'concat'
hidden_size = 500
encoder_n_layers = 2
decoder_n_layers = 2
dropout = 0.1
batch_size = 64

# Set checkpoint to load from; set to None if starting from scratch
loadFilename = None
checkpoint_iter = 4000

print('Building encoder and decoder ...')
# Initialize word embeddings
embedding = nn.Embedding(voc.num_words, hidden_size)

# Initialize encoder & decoder models
encoder = EncoderRNN(hidden_size, embedding, encoder_n_layers, dropout)
decoder = LuongAttnDecoderRNN(attn_model, embedding, hidden_size, voc.num_words, 
                              decoder_n_layers, dropout)

# Use appropriate device
encoder = encoder.to(device)
decoder = decoder.to(device)
print('Models built and ready to go!')

Building encoder and decoder ...
Models built and ready to go!


# Run Training

First we set training parameters, then we initialize our optimizers, and finally we call the trainIters function to run our training iterations.

In [65]:
# Configure training/optimization
clip = 50.0
teacher_forcing_ratio = 1.0
learning_rate = 0.0001
decoder_learning_ratio = 5.0
n_iteration = 4000
print_every = 1
save_every = 500

# Ensure dropout layers are in train mode
encoder.train()
decoder.train()

# Initialize optimizers
print('Building optimizers ...')
encoder_optimizer = optim.Adam(encoder.parameters(), lr=learning_rate)
decoder_optimizer = optim.Adam(decoder.parameters(), lr=learning_rate * decoder_learning_ratio)

# If you have cuda, configure cuda to call
for state in encoder_optimizer.state.values():
    for k, v in state.items():
        if isinstance(v, torch.Tensor):
            state[k] = v.cuda()

for state in decoder_optimizer.state.values():
    for k, v in state.items():
        if isinstance(v, torch.Tensor):
            state[k] = v.cuda()

# Run training iterations
print("Starting Training!")
save_dir = None
corpus_name = None
trainIteration(model_name, voc, pairs, encoder, decoder, encoder_optimizer, decoder_optimizer,
           embedding, encoder_n_layers, decoder_n_layers, save_dir, n_iteration, batch_size,
           print_every, save_every, clip, corpus_name, loadFilename)

Building optimizers ...
Starting Training!
Initializing Iteration's...
Start Training...
Iteration: 1; Percent complete: 0.0%; Average loss: 8.9378
Iteration: 2; Percent complete: 0.1%; Average loss: 8.7510
Iteration: 3; Percent complete: 0.1%; Average loss: 8.4597
Iteration: 4; Percent complete: 0.1%; Average loss: 8.0706


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 5; Percent complete: 0.1%; Average loss: 7.5536
Iteration: 6; Percent complete: 0.1%; Average loss: 7.1166
Iteration: 7; Percent complete: 0.2%; Average loss: 6.5440
Iteration: 8; Percent complete: 0.2%; Average loss: 6.7577
Iteration: 9; Percent complete: 0.2%; Average loss: 6.6333


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 10; Percent complete: 0.2%; Average loss: 6.2479
Iteration: 11; Percent complete: 0.3%; Average loss: 5.7861
Iteration: 12; Percent complete: 0.3%; Average loss: 5.6518
Iteration: 13; Percent complete: 0.3%; Average loss: 5.5241
Iteration: 14; Percent complete: 0.4%; Average loss: 5.4355


...

/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 3987; Percent complete: 99.7%; Average loss: 2.3648
Iteration: 3988; Percent complete: 99.7%; Average loss: 2.3685
Iteration: 3989; Percent complete: 99.7%; Average loss: 2.2144
Iteration: 3990; Percent complete: 99.8%; Average loss: 2.5074
Iteration: 3991; Percent complete: 99.8%; Average loss: 2.4931


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 3992; Percent complete: 99.8%; Average loss: 2.2304
Iteration: 3993; Percent complete: 99.8%; Average loss: 2.2865
Iteration: 3994; Percent complete: 99.9%; Average loss: 2.5235
Iteration: 3995; Percent complete: 99.9%; Average loss: 2.4959
Iteration: 3996; Percent complete: 99.9%; Average loss: 2.3592
Iteration: 3997; Percent complete: 99.9%; Average loss: 2.4609
Iteration: 3998; Percent complete: 100.0%; Average loss: 2.3826
Iteration: 3999; Percent complete: 100.0%; Average loss: 2.5507
Iteration: 4000; Percent complete: 100.0%; Average loss: 2.4809


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:70: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

# Run Evaluation for chating

In [0]:
# Set dropout layers to eval mode
encoder.eval()
decoder.eval()

# Initialize search module
searcher = GreedySearchDecoder(encoder, decoder)
print("Hey User I am Ankit Desai :) \n Let's Start Chatting ....")
evaluateInput(encoder, decoder, searcher, voc)